<a href="https://colab.research.google.com/github/jo1jun/Human-Action-Recog-VIBE/blob/main/HMAR_Demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Google Drive Mount

In [ ]:
from google.colab import drive 
drive.mount('/content/drive')

Mounted at /content/drive


# Prepare VIBE


In [ ]:
# Clone the repo
!git clone https://github.com/mkocabas/VIBE.git
%cd VIBE/
# Install the other requirements
!pip install torch==1.4.0 numpy==1.17.5
!pip install git+https://github.com/giacaglia/pytube.git --upgrade
!pip install -r requirements.txt
# Download pretrained weights and SMPL data
!source scripts/prepare_data.sh

Cloning into 'VIBE'...
remote: Enumerating objects: 408, done.
remote: Counting objects: 100% (35/35), done.
remote: Compressing objects: 100% (35/35), done.
remote: Total 408 (delta 15), reused 5 (delta 0), pack-reused 373
Receiving objects: 100% (408/408), 15.11 MiB | 41.15 MiB/s, done.
Resolving deltas: 100% (184/184), done.
/content/VIBE
     |████████████████████████████████| 753.4 MB 6.2 kB/s 
     |████████████████████████████████| 20.0 MB 625 kB/s 
  Attempting uninstall: torch
    Found existing installation: torch 1.10.0+cu111
    Uninstalling torch-1.10.0+cu111:
      Successfully uninstalled torch-1.10.0+cu111
  Attempting uninstall: numpy
    Found existing installation: numpy 1.19.5
    Uninstalling numpy-1.19.5:
      Successfully uninstalled numpy-1.19.5
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torchvision 0.11.1+cu111 requires torch==1.1

  Cloning https://github.com/giacaglia/pytube.git to /tmp/pip-req-build-3y745i8w
  Running command git clone -q https://github.com/giacaglia/pytube.git /tmp/pip-req-build-3y745i8w
  Created wheel for pytube: filename=pytube-9.5.3-py3-none-any.whl size=32290 sha256=3e0d5f8e73c1362c03b85119cacb2f8d29ae077e178ad9201131b33e0361c462
  Stored in directory: /tmp/pip-ephem-wheel-cache-1j0_twsi/wheels/ca/b9/e4/f14415300036c42fae7c12b5dd718f0e8a10e29184fc82eb47
Successfully built pytube
  Cloning https://github.com/mattloper/chumpy.git to /tmp/pip-req-build-spq7tm01
  Running command git clone -q https://github.com/mattloper/chumpy.git /tmp/pip-req-build-spq7tm01
  Cloning https://github.com/mkocabas/yolov3-pytorch.git to /tmp/pip-req-build-i6djcu7k
  Running command git clone -q https://github.com/mkocabas/yolov3-pytorch.git /tmp/pip-req-build-i6djcu7k
  Cloning https://github.com/mkocabas/multi-person-tracker.git to /tmp/pip-req-build-qx3k566j
  Running command git clone -q https://github.com/

Downloading...
From: https://drive.google.com/uc?id=1untXhYOLQtpNEy4GTY_0fL_H-k6cTf_r
To: /content/VIBE/data/vibe_data.zip
100% 561M/561M [00:04<00:00, 138MB/s]
Archive:  vibe_data.zip
   creating: vibe_data/
  inflating: vibe_data/smpl_mean_params.npz  
  inflating: vibe_data/vibe_model_w_3dpw.pth.tar  
  inflating: vibe_data/gmm_08.pkl    
  inflating: vibe_data/J_regressor_h36m.npy  
  inflating: vibe_data/vibe_model_wo_3dpw.pth.tar  
  inflating: vibe_data/SMPL_NEUTRAL.pkl  
  inflating: vibe_data/J_regressor_extra.npy  
  inflating: vibe_data/spin_model_checkpoint.pth.tar  
  inflating: vibe_data/sample_video.mp4  
  inflating: vibe_data/yolov3.weights  


In [ ]:
!gdown --id 12bkjxB9AZqSXHUHXwXq3YwmoW_z42qml --output sample.mp4
!gdown --id 1-Iotn5YExp6qcYPqO5e8ngdrej_nf86C --output ViT_Classifier.pt

Downloading...
From: https://drive.google.com/uc?id=12bkjxB9AZqSXHUHXwXq3YwmoW_z42qml
To: /content/VIBE/sample.mp4
100% 5.33M/5.33M [00:00<00:00, 84.2MB/s]
Downloading...
From: https://drive.google.com/uc?id=1-Iotn5YExp6qcYPqO5e8ngdrej_nf86C
To: /content/VIBE/ViT_Classifier.pt
100% 1.25M/1.25M [00:00<00:00, 79.4MB/s]


- caution


device & torch version must be cuda & 1.4.0 respectively.

If torch version is not 1.4.0, restart runtime(ctrl + M) and run from below cell.

In [ ]:
import torch
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
print(device)
print(torch.__version__)

SEQLEN = 32
num_class = 3

# Input your height & weight.

# 키는 m 단위로 기입. ex) 175cm -> 1.75
# 체중은 kg 단위로 기입. ex) 75kg -> 75
HEIGHT = 1.75
WEIGHT = 75

BMI = -1.0
if HEIGHT != 0 and WEIGHT != 0:
    BMI = WEIGHT / (HEIGHT * HEIGHT)

# -1 : BMI 구할 수 없음, 0 : 심한 저체중, 1 : 저체중, 2 : 정상, 3 : 과체중, 4 : 심한과체중
real_fatness = 0
if BMI == -1:
    real_fatness = -1
elif 0 <= BMI and BMI <= 15.0:
    real_fatness = 0
elif BMI < 18.5:
    real_fatness = 1
elif BMI < 23:
    real_fatness = 2
elif BMI < 25:
    real_fatness = 3
else:
    real_fatness = 4

print(real_fatness)

%cd /content/VIBE

cuda
1.4.0
3
/content/VIBE


# Service Module

In [ ]:
# -*- coding: utf-8 -*-

# Max-Planck-Gesellschaft zur Förderung der Wissenschaften e.V. (MPG) is
# holder of all proprietary rights on this computer program.
# You can only use this computer program if you have closed
# a license agreement with MPG or you get the right to use the computer
# program from someone who is authorized to grant you that right.
# Any use of the computer program without a valid license is prohibited and
# liable to prosecution.
#
# Copyright©2019 Max-Planck-Gesellschaft zur Förderung
# der Wissenschaften e.V. (MPG). acting on behalf of its Max Planck Institute
# for Intelligent Systems. All rights reserved.
#
# Contact: ps-license@tuebingen.mpg.de

import os
os.environ['PYOPENGL_PLATFORM'] = 'egl'

import cv2
import time
import torch
import joblib
import shutil
import colorsys
import argparse
import numpy as np
from collections import OrderedDict
from tqdm import tqdm
from multi_person_tracker import MPT
from torch.utils.data import DataLoader

from lib.models.vibe import VIBE_Demo
from lib.utils.renderer import Renderer
from lib.dataset.inference import Inference
from lib.utils.smooth_pose import smooth_pose
from lib.data_utils.kp_utils import convert_kps
from lib.utils.pose_tracker import run_posetracker

from lib.utils.demo_utils import (
    download_youtube_clip,
    smplify_runner,
    convert_crop_coords_to_orig_img,
    convert_crop_cam_to_orig_img,
    prepare_rendering_results,
    video_to_images,
    images_to_video,
    download_ckpt,
)

MIN_NUM_FRAMES = SEQLEN

- video to image sequences

In [ ]:
# Upload your mixed action (run, punch, squat) video at '/content/VIBE' and revise below line
VIDEO_FILE = '/content/VIBE/sample.mp4'

output_path = os.path.join("./output/", os.path.basename(VIDEO_FILE).replace('.mp4', ''))
os.makedirs(output_path, exist_ok=True)

image_folder, num_frames, img_shape = video_to_images(VIDEO_FILE, return_info=True)

print(f'Input video number of frames {num_frames}')
orig_height, orig_width = img_shape[:2]

total_time = time.time()

Running "ffmpeg -i /content/VIBE/sample.mp4 -f image2 -v error /tmp/sample_mp4/%06d.png"
Images saved to "/tmp/sample_mp4"
Input video number of frames 561


- Run tracking

In [ ]:
bbox_scale = 1.1

# run multi object tracker
tracker_batch_size = 12
detector = "yolo"
yolo_img_size = 416

mot = MPT(
    device=device,
    batch_size=tracker_batch_size,
    display=False,
    detector_type=detector,
    output_format='dict',
    yolo_img_size=yolo_img_size,
)
tracking_results = mot(image_folder)

# remove tracklets if num_frames is less than MIN_NUM_FRAMES
for person_id in list(tracking_results.keys()):
    if tracking_results[person_id]['frames'].shape[0] < MIN_NUM_FRAMES:
        del tracking_results[person_id]

print(tracking_results)

  0%|          | 0/47 [00:00<?, ?it/s]

Running Multi-Person-Tracker


100%|██████████| 47/47 [00:15<00:00,  3.17it/s]

Finished. Detection + Tracking FPS 35.06
{1: {'bbox': array([[469.91070557, 292.55701447, 253.83976348, 253.83976348],
       [470.45834984, 292.18279953, 254.77989587, 254.77989587],
       [470.91132314, 291.91672589, 255.76829511, 255.76829511],
       ...,
       [483.46174336, 290.21555038, 266.55631683, 266.55631683],
       [483.98872098, 290.38243817, 264.7385152 , 264.7385152 ],
       [483.86529553, 290.29695215, 263.85384518, 263.85384518]]), 'frames': array([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,
        39,  40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,
        52,  53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,
        65,  66,  67,  68,  69,  70,  71,  72,  73,  74,  75,  76,  77,
        78,  79,  80,  81,  82,  83,  84,  85,  86,  87,  88,  89,  90,
        91,  92,  93,  94,  

- Run VIBE model

In [ ]:
# ========= Define VIBE model ========= #
model = VIBE_Demo(
    seqlen=SEQLEN,
    n_layers=2,
    hidden_size=1024,
    add_linear=True,
    use_residual=True,
).to(device)

# ========= Load pretrained weights ========= #
pretrained_file = download_ckpt(use_3dpw=False)
ckpt = torch.load(pretrained_file)
print(f'Performance of pretrained model on 3DPW: {ckpt["performance"]}')
ckpt = ckpt['gen_state_dict']
model.load_state_dict(ckpt, strict=False)
model.eval()
print(f'Loaded pretrained weights from \"{pretrained_file}\"')

# ========= Run VIBE on each person ========= #
print(f'Running VIBE on each tracklet...')
vibe_time = time.time()
vibe_results = {}
tracking_method = 'bbox'
vibe_batch_size = 450

for person_id in tqdm(list(tracking_results.keys())):
    bboxes = joints2d = None

    if tracking_method == 'bbox':
        bboxes = tracking_results[person_id]['bbox']
        

    frames = tracking_results[person_id]['frames']

    dataset = Inference(
        image_folder=image_folder,
        frames=frames,
        bboxes=bboxes,
        joints2d=joints2d,
        scale=bbox_scale,
    )

    bboxes = dataset.bboxes
    frames = dataset.frames
    has_keypoints = True if joints2d is not None else False

    dataloader = DataLoader(dataset, batch_size=vibe_batch_size, num_workers=16)

    with torch.no_grad():

        pred_cam, pred_verts, pred_pose, pred_betas, pred_joints3d, smpl_joints2d, norm_joints2d = [], [], [], [], [], [], []

        for batch in dataloader:
            if has_keypoints:
                batch, nj2d = batch
                norm_joints2d.append(nj2d.numpy().reshape(-1, 21, 3))

            batch = batch.unsqueeze(0)
            batch = batch.to(device)

            batch_size, seqlen = batch.shape[:2]
            output = model(batch)[-1]

            pred_cam.append(output['theta'][:, :, :3].reshape(batch_size * seqlen, -1))
            pred_verts.append(output['verts'].reshape(batch_size * seqlen, -1, 3))
            pred_pose.append(output['theta'][:,:,3:75].reshape(batch_size * seqlen, -1))
            pred_betas.append(output['theta'][:, :,75:].reshape(batch_size * seqlen, -1))
            pred_joints3d.append(output['kp_3d'].reshape(batch_size * seqlen, -1, 3))
            smpl_joints2d.append(output['kp_2d'].reshape(batch_size * seqlen, -1, 2))


        pred_cam = torch.cat(pred_cam, dim=0)
        pred_verts = torch.cat(pred_verts, dim=0)
        pred_pose = torch.cat(pred_pose, dim=0)
        pred_betas = torch.cat(pred_betas, dim=0)
        pred_joints3d = torch.cat(pred_joints3d, dim=0)
        smpl_joints2d = torch.cat(smpl_joints2d, dim=0)
        del batch

    # ========= Save results to a pickle file ========= #
    pred_cam = pred_cam.cpu().numpy()
    pred_verts = pred_verts.cpu().numpy()
    pred_pose = pred_pose.cpu().numpy()
    pred_betas = pred_betas.cpu().numpy()
    pred_joints3d = pred_joints3d.cpu().numpy()
    smpl_joints2d = smpl_joints2d.cpu().numpy()


    orig_cam = convert_crop_cam_to_orig_img(
        cam=pred_cam,
        bbox=bboxes,
        img_width=orig_width,
        img_height=orig_height
    )

    joints2d_img_coord = convert_crop_coords_to_orig_img(
        bbox=bboxes,
        keypoints=smpl_joints2d,
        crop_size=224,
    )

    output_dict = {
        'pred_cam': pred_cam,
        'orig_cam': orig_cam,
        'verts': pred_verts,
        'pose': pred_pose,
        'betas': pred_betas,
        'joints3d': pred_joints3d,
        'joints2d': joints2d,
        'joints2d_img_coord': joints2d_img_coord,
        'bboxes': bboxes,
        'frame_ids': frames,
    }

    vibe_results[person_id] = output_dict

del model

end = time.time()
fps = num_frames / (end - vibe_time)

print('vibe_results', vibe_results)

print(f'VIBE FPS: {fps:.2f}')
total_time = time.time() - total_time
print(f'Total time spent: {total_time:.2f} seconds (including model loading time).')
print(f'Total FPS (including model loading time): {num_frames / total_time:.2f}.')
print(f'Saving output results to \"{os.path.join(output_path, "vibe_output.pkl")}\".')
joblib.dump(vibe_results, os.path.join(output_path, "vibe_output.pkl"))


Downloading: "https://download.pytorch.org/models/resnet50-19c8e357.pth" to /root/.cache/torch/checkpoints/resnet50-19c8e357.pth



=> loaded pretrained model from 'data/vibe_data/spin_model_checkpoint.pth.tar'


  0%|          | 0/1 [00:00<?, ?it/s]

Performance of pretrained model on 3DPW: 56.56075477600098
Loaded pretrained weights from "data/vibe_data/vibe_model_wo_3dpw.pth.tar"
Running VIBE on each tracklet...


100%|██████████| 1/1 [00:06<00:00,  6.59s/it]

vibe_results {1: {'pred_cam': array([[ 1.210866  , -0.0108385 ,  0.16634855],
       [ 1.2375531 , -0.01351677,  0.1728805 ],
       [ 1.2475973 , -0.01135522,  0.1757794 ],
       ...,
       [ 1.1338211 , -0.26133373,  0.11814048],
       [ 1.1416944 , -0.2639489 ,  0.11299142],
       [ 1.1634741 , -0.26172835,  0.12593462]], dtype=float32), 'orig_cam': array([[0.36075814, 0.64034569, 0.27488416, 0.50833189],
       [0.37007471, 0.65688261, 0.26848662, 0.50388078],
       [0.37452564, 0.66478301, 0.2701359 , 0.50117835],
       ...,
       [0.35472674, 0.62963997, 0.11892156, 0.45044381],
       [0.35475409, 0.62968852, 0.11976411, 0.44637344],
       [0.36031351, 0.63955648, 0.11526009, 0.45361581]]), 'verts': array([[[ 0.02770237, -0.9579059 , -0.1938408 ],
        [ 0.02375442, -0.9443362 , -0.20161024],
        [ 0.03429116, -0.9407085 , -0.19210929],
        ...,
        [-0.09367375, -0.89087135, -0.11213937],
        [-0.09405673, -0.8926741 , -0.11375247],
        [-0.096391

['./output/sample/vibe_output.pkl']

- VIBE output을 classifier input 형태로 변환시키기.

In [ ]:
persion_id = list(vibe_results.keys())[0]
vibe_pose_data = vibe_results[person_id]['pose']

print(vibe_pose_data.shape)
print(vibe_pose_data)

WINDOW_SIZE = SEQLEN
pose_data_list = vibe_pose_data.tolist()
print(pose_data_list)

classifier_data = []
for i in range(0, len(pose_data_list) - WINDOW_SIZE + 1):
    tmp = []
    for j in range(WINDOW_SIZE):
        tmp.append(pose_data_list[i+j])
    classifier_data.append(tmp)

classifier_data = np.array(classifier_data)
print(classifier_data.shape)

(561, 72)
[[-3.1092048   0.05261758 -0.12224633 ... -0.04990197 -0.04143471
   0.35616374]
 [-3.0898972   0.04857596 -0.13910845 ... -0.05695927 -0.03891411
   0.34734675]
 [-3.096428    0.03593709 -0.10303032 ... -0.05892446 -0.03892878
   0.33740503]
 ...
 [-1.9213569   0.13629948 -2.4250145  ...  0.18250212 -0.12810487
   0.40381658]
 [-2.1409504   0.08162989 -2.285076   ...  0.16843067 -0.12062616
   0.39997825]
 [-1.9768134   0.13203715 -2.4110599  ...  0.15894821 -0.13085711
   0.38434413]]
[[-3.1092047691345215, 0.052617575973272324, -0.12224632501602173, -0.136263906955719, -0.010657279752194881, 0.03634481877088547, -0.18809008598327637, 0.0005428416770882905, -0.028332870453596115, 0.21901561319828033, -0.0006998048629611731, 0.0033278577029705048, 0.2685469686985016, 0.018409842625260353, -0.07795698940753937, 0.30580928921699524, -0.07170739024877548, 0.007963563315570354, 0.01838727667927742, -0.02468203939497471, 0.006936090067028999, -0.1974112093448639, 0.15595841407775

# Classifier(ViT)

In [ ]:
import torch
import torch.nn as nn
%pip install einops
from einops import rearrange, repeat, reduce

In [ ]:
class MultiHeadAttentionLayer(nn.Module):
    def __init__(self, d_model, nhead, dropout_ratio):
        super().__init__()

        self.d_model = d_model # d_model : embed dimension
        self.nhead = nhead # nhead : head 수
        self.head_dim = d_model // nhead # head_dim : head 마다의 dimension

        # 위 figure 에서 Q, K, V 가 head 수 만큼의 Linear 를 거쳐 Scaled Dot-Product Attention에 들어가는데
        # 실제 구현에서는 Q, K, V 각각이 하나의 Linear 를 거쳐 나온 것을 쪼개서 Scaled Dot-Product Attention에 들어가게 함.
        self.qLinear = nn.Linear(d_model, d_model) # query lineqr
        self.kLinear = nn.Linear(d_model, d_model) # key linear
        self.vLinear = nn.Linear(d_model, d_model) # value linear

        self.oLinear = nn.Linear(d_model, d_model) # output linear

        self.dropout = nn.Dropout(dropout_ratio)

    def forward(self, query, key, value): # 기존의 Transformer 와 달리 mask 없음.

        batch_size = query.shape[0]
        query_len = query.shape[1]
        value_len = key_len = key.shape[1]

        # query: [batch_size, query_len, d_model]
        # key: [batch_size, key_len, d_model]
        # value: [batch_size, value_len, d_model]
 
        Q = self.qLinear(query)
        K = self.kLinear(key)
        V = self.vLinear(value)

        # Q: [batch_size, query_len, d_model]
        # K: [batch_size, key_len, d_model]
        # V: [batch_size, value_len, d_model]

        # d_model = nhead * head_dim
        # head 수로 distribute
        Q = rearrange(Q, 'b l (h d) -> b h l d', h=self.nhead)
        K = rearrange(K, 'b l (h d) -> b h l d', h=self.nhead)
        V = rearrange(V, 'b l (h d) -> b h l d', h=self.nhead)

        # Q: [batch_size, nhead, query_len, head_dim]
        # K: [batch_size, nhead, key_len, head_dim]
        # V: [batch_size, nhead, value_len, head_dim]

        #=========Scaled Dot-Product Attention=========

        # attention weight 계산
        weight = torch.matmul(Q, rearrange(K, 'b h l d -> b h d l')) / np.sqrt(self.head_dim)

        # weight: [batch_size, nhead, query_len, key_len]

        attention = torch.softmax(weight, dim=-1)

        # attention: [batch_size, nhead, query_len, key_len]

        # context vector 계산
        c = torch.matmul(self.dropout(attention), V)

        # c: [batch_size, nhead, query_len, head_dim]

        #=========Scaled Dot-Product Attention=========

        # reshape & concat
        c = rearrange(c, 'b h l d -> b l (h d)')

        # c: [batch_size, query_len, d_model]

        output = self.oLinear(c)

        # output: [batch_size, query_len, d_model]

        return output, attention

In [ ]:
class PositionWiseFeedForwardLayer(nn.Module):
    def __init__(self, d_model, ff_dim, dropout_ratio):
        super().__init__()
        # ff_dim : FFN 에서 hidden layer node 수
        self.linear1 = nn.Linear(d_model, ff_dim)
        self.linear2 = nn.Linear(ff_dim, d_model)

        self.dropout = nn.Dropout(dropout_ratio)

    def forward(self, x):

        # x: [batch_size, seq_len, d_model]

        # The MLP contains two layers with a GELU non-linearity
        x = self.dropout(nn.functional.gelu(self.linear1(x)))

        # x: [batch_size, seq_len, ff_dim]

        x = self.linear2(x)

        # x: [batch_size, seq_len, d_model]

        return x

In [ ]:
class EncoderLayer(nn.Module):
    def __init__(self, d_model, nhead, ff_dim, dropout_ratio):
        super().__init__()

        self.layerNorm1 = nn.LayerNorm(d_model)
        self.layerNorm2 = nn.LayerNorm(d_model)
        self.multiHeadAttentionLayer = MultiHeadAttentionLayer(d_model, nhead, dropout_ratio)
        self.positionWiseFeedForward = PositionWiseFeedForwardLayer(d_model, ff_dim, dropout_ratio)
        self.dropout = nn.Dropout(dropout_ratio)

    def forward(self, src):

        # src: [batch_size, src_len, d_model] # encoder layer 에 입력되는 값

        # Layernorm (LN) is applied before every block
        _src = self.layerNorm1(src)

        # self attention 이므로 query, key, value 전부 동일
        _src, attention = self.multiHeadAttentionLayer(_src, _src, _src)

        # residual connections after every block

        # Dropout, when used, is applied after every dense layer except for the the qkv-projections
        # and directly after adding positional- to patch embeddings. 
        src = src + self.dropout(_src)

        _src = self.layerNorm2(src)

        # src: [batch_size, src_len, d_model]

        _src = self.positionWiseFeedForward(_src)

        src = src + self.dropout(_src)

        # src: [batch_size, src_len, d_model]

        return src, attention

In [ ]:
class Encoder(nn.Module):
    def __init__(self, d_model, n_layers, nhead, ff_dim, dropout_ratio):
        super().__init__()
        # n_layers : encoder layer 반복 수
        # Encoder Layer 을 n_layers 만큼 반복.
        self.layers = nn.ModuleList([EncoderLayer(d_model, nhead, ff_dim, dropout_ratio) for _ in range(n_layers)])

    def forward(self, src):

        # src: [batch_size, src_len, d_model]

        for layer in self.layers:
            src, attention = layer(src)

        # src: [batch_size, src_len, d_model]

        return src, attention

In [ ]:
class ImageEmbedding(nn.Module):
  def __init__(self, seqlen, pose_dim, D):
    super().__init__()
    # 임베딩 작업 [batch_size, seqlen, pose_dim] -> [batch_size, seqlen, embed_dim]
    self.linear = nn.Linear(pose_dim, D)
    # learnable cls_token (only for classification)
    self.cls_token = nn.Parameter(torch.randn(1, 1, D))

  def forward(self, x):

    batch_size, seqlen, pose_dim = x.shape
    # x: [batch_size, seqlen, pose_dim]

    embedded_patches = self.linear(x)
    # embedded_patches : [batch_size, seqlen, embed_dim]
    
    # Similar to BERT’s [class] token, we prepend a learnable embedding to the sequence of embedded patches
    # classification 의 경우 맨 앞에 learnable cls_token 추가.
    cls_tokens = repeat(self.cls_token, 'b n d -> (b repeat) n d', repeat=batch_size)
    embedded_patches = torch.cat((cls_tokens, embedded_patches), dim=1)

    # embedded_patches : [batch_size, 1 + seqlen, embed_dim]

    return embedded_patches

In [ ]:
class TokPosEmbedding(nn.Module):
  def __init__(self, seqlen, pose_dim, d_model, dropout_ratio):
    super().__init__()
    self.tokEmbedding = ImageEmbedding(seqlen, pose_dim, d_model)
    self.posEmbedding = nn.Embedding(100, d_model) # cos & sin positional encoding 대신, learnable positional embedding 으로 구현. (max patch 수 100)
                                                   # max length : 입력 sequence 의 최대 길이.
    self.d_model = d_model
    self.dropout = nn.Dropout(dropout_ratio)

  def forward(self, src):

    # src: [batch_size, seqlen. pose_dim]

    src = self.tokEmbedding(src)

    # src: [batch_size, src_len, d_model]

    batch_size = src.shape[0]
    src_len = src.shape[1]

    # 0 ~ src_len 등차 수열값 을 bactch 한개와 동일한 shape으로 생성 (positional embedding)
    pos = torch.arange(0, src_len, dtype=torch.long) # pos: [src_len]
    pos = repeat(pos, 'l -> b l', b=batch_size).to(device) # pos: [batch_size, src_len]

    src = self.dropout(src * float(np.sqrt(self.d_model)) + self.posEmbedding(pos))
    # Dropout, when used, is applied after every dense layer except for the the qkv-projections and directly after adding positional- to patch embeddings

    # src: [batch_size, src_len, d_model]

    return src

In [ ]:
class VisionTransformer(nn.Module):
    def __init__(self, seqlen, pose_dim, d_model, n_layers, nhead, ff_dim, dropout_ratio, output_dim):
        super().__init__()

        self.encEmbedding = TokPosEmbedding(seqlen, pose_dim, d_model, dropout_ratio)
        self.encoder = Encoder(d_model, n_layers, nhead, ff_dim, dropout_ratio)
        self.layerNorm = nn.LayerNorm(d_model)
        self.linear = nn.Linear(d_model, output_dim) 

    def forward(self, src):
        
        # image: [batch_size, seqlen. pose_dim]

        src = self.encEmbedding(src)

        # src: [batch_size, src_len, d_model]

        enc_src, attention = self.encoder(src)

        # enc_src: [batch_size, src_len, d_model] # encoder의 출력값.

        # classification head

        enc_src = enc_src[:,0,:] # cls tokken

        # enc_src: [batch_size, d_model]

        enc_src = self.layerNorm(enc_src)

        output = self.linear(enc_src)

        # output: [batch_size, output_dim]

        return output, attention

In [ ]:
import torch.nn as nn

class Classifier(nn.Module):
  def __init__(self, seqlen = 32):
    super().__init__()
    self.ViT = VisionTransformer(seqlen, 72, 64, 2, 2, 1024, 0.25, 3)

  def forward(self, parameters):
    output = self.ViT(parameters)

    return output

In [ ]:
classifier = Classifier()

In [ ]:
classifier.load_state_dict(torch.load('/content/VIBE/ViT_Classifier.pt'))
classifier = classifier.to('cuda')
classifier.eval()

Classifier(
  (ViT): VisionTransformer(
    (encEmbedding): TokPosEmbedding(
      (tokEmbedding): ImageEmbedding(
        (linear): Linear(in_features=72, out_features=64, bias=True)
      )
      (posEmbedding): Embedding(100, 64)
      (dropout): Dropout(p=0.25, inplace=False)
    )
    (encoder): Encoder(
      (layers): ModuleList(
        (0): EncoderLayer(
          (layerNorm1): LayerNorm((64,), eps=1e-05, elementwise_affine=True)
          (layerNorm2): LayerNorm((64,), eps=1e-05, elementwise_affine=True)
          (multiHeadAttentionLayer): MultiHeadAttentionLayer(
            (qLinear): Linear(in_features=64, out_features=64, bias=True)
            (kLinear): Linear(in_features=64, out_features=64, bias=True)
            (vLinear): Linear(in_features=64, out_features=64, bias=True)
            (oLinear): Linear(in_features=64, out_features=64, bias=True)
            (dropout): Dropout(p=0.25, inplace=False)
          )
          (positionWiseFeedForward): PositionWiseFeedFor

# Estimation(ViT)

In [ ]:
classifier_data = torch.Tensor(classifier_data)
classifier_data = classifier_data.to('cuda')
with torch.no_grad():
  output, _ = classifier(classifier_data)
  _, preds = torch.max(output, 1)
  print(preds)
  # 0 : Run / 1 : Punch / 2 : Squat

tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,

In [ ]:
preds = np.array(preds.cpu())

In [ ]:
print(preds.shape)

(530,)


# Final Classification (Voting)

In [ ]:
frame_length = len(preds) + SEQLEN - 1
print(frame_length)

561


In [ ]:
vote_dict_list = []

for i in range(frame_length):
  vote_dict = np.zeros(num_class)
  vote_dict_list.append(vote_dict)

for i in range(preds.shape[0]):
  for j in range(SEQLEN):
      vote_dict_list[i+j][preds[i]] += 1

In [ ]:
print(vote_dict_list)

[array([1., 0., 0.]), array([2., 0., 0.]), array([3., 0., 0.]), array([4., 0., 0.]), array([5., 0., 0.]), array([6., 0., 0.]), array([7., 0., 0.]), array([8., 0., 0.]), array([9., 0., 0.]), array([10.,  0.,  0.]), array([11.,  0.,  0.]), array([12.,  0.,  0.]), array([13.,  0.,  0.]), array([14.,  0.,  0.]), array([15.,  0.,  0.]), array([16.,  0.,  0.]), array([17.,  0.,  0.]), array([18.,  0.,  0.]), array([19.,  0.,  0.]), array([20.,  0.,  0.]), array([21.,  0.,  0.]), array([22.,  0.,  0.]), array([23.,  0.,  0.]), array([24.,  0.,  0.]), array([25.,  0.,  0.]), array([26.,  0.,  0.]), array([27.,  0.,  0.]), array([28.,  0.,  0.]), array([29.,  0.,  0.]), array([30.,  0.,  0.]), array([31.,  0.,  0.]), array([32.,  0.,  0.]), array([32.,  0.,  0.]), array([32.,  0.,  0.]), array([32.,  0.,  0.]), array([32.,  0.,  0.]), array([32.,  0.,  0.]), array([32.,  0.,  0.]), array([32.,  0.,  0.]), array([32.,  0.,  0.]), array([32.,  0.,  0.]), array([32.,  0.,  0.]), array([32.,  0.,  

In [ ]:
final_preds = []

max_idx = num_class - 1 # class 개수 - 1
for idx, vote_dict in enumerate(vote_dict_list):
  if np.argmax(vote_dict) != max_idx - np.argmax(np.flip(vote_dict)): # 투표된 action 개수가 동일한 경우
    final_preds.append(final_preds[idx-1]) # 이전 action 할당
  else:  
    final_preds.append(np.argmax(vote_dict))

print(len(preds))
print(np.bincount(preds))
print(len(final_preds))
print(np.bincount(final_preds))

530
[272  78 180]
561
[288  93 180]


In [ ]:
run_percentage = np.bincount(final_preds)[0] / len(final_preds) * 100
try: 
  punch_percentage = np.bincount(final_preds)[1] / len(final_preds) * 100
except:
  punch_percentage = 0
try: 
  squat_percentage = np.bincount(final_preds)[2] / len(final_preds) * 100
except:
  squat_percentage = 0

print("Run    :  {:.2f} %".format(run_percentage))
print("Punch  :  {:.2f} %".format(punch_percentage))
print("Squat  :  {:.2f} %".format(squat_percentage))

Run    :  51.34 %
Punch  :  16.58 %
Squat  :  32.09 %


# visualization

In [ ]:
def prepare_rendering_results_2(vibe_results, nframes):
    frame_results = [{} for _ in range(nframes)]
    for person_id, person_data in vibe_results.items():
        for idx, frame_id in enumerate(person_data['frame_ids']):
            frame_results[frame_id][person_id] = {
                'verts': person_data['verts'][idx],
                'cam': person_data['orig_cam'][idx],
                'bboxes': person_data['bboxes'][idx],
            }

    # naive depth ordering based on the scale of the weak perspective camera
    for frame_id, frame_data in enumerate(frame_results):
        # sort based on y-scale of the cam in original image coords
        sort_idx = np.argsort([v['cam'][1] for k,v in frame_data.items()])
        frame_results[frame_id] = OrderedDict(
            {list(frame_data.keys())[i]:frame_data[list(frame_data.keys())[i]] for i in sort_idx}
        )

    return frame_results



no_render = False

if not no_render:
    # ========= Render results as a single video ========= #
    wireframe = False
    renderer = Renderer(resolution=(orig_width, orig_height), orig_img=True, wireframe=wireframe)

    output_img_folder = f'{image_folder}_output'
    os.makedirs(output_img_folder, exist_ok=True)

    print(f'Rendering output video, writing frames to {output_img_folder}')

    # prepare results for rendering
    frame_results = prepare_rendering_results_2(vibe_results, num_frames)
    mesh_color = {k: colorsys.hsv_to_rgb(np.random.rand(), 0.5, 1.0) for k in vibe_results.keys()}

    image_file_names = sorted([
        os.path.join(image_folder, x)
        for x in os.listdir(image_folder)
        if x.endswith('.png') or x.endswith('.jpg')
    ])

    sideview = False
    display = False
    save_obj = False

    actions_cnt = [0, 0, 0]
    actions = ["run", 'punch', 'squat']

    for frame_idx in tqdm(range(len(image_file_names))):
        img_fname = image_file_names[frame_idx]
        img = cv2.imread(img_fname)
            

        if sideview:
            side_img = np.zeros_like(img)

        for person_id, person_data in frame_results[frame_idx].items():
            frame_verts = person_data['verts']
            frame_cam = person_data['cam']
            frame_bboxes = person_data['bboxes']
            try:
              frame_actions = final_preds[frame_idx]
            except:
              break

            actions_cnt[frame_actions] += 1

            mc = mesh_color[person_id]

            # visualization bbox
            center_x, center_y, width, height = frame_bboxes

            left_top = (int(center_x - width/2), int(center_y - height/2))
            right_bot = (int(center_x + width/2), int(center_y + height/2))
            img = cv2.rectangle(img, left_top, right_bot, mc, 3)
            img = cv2.putText(img, actions[frame_actions], (left_top[0], left_top[1] - 5), cv2.FONT_HERSHEY_SIMPLEX, 0.8, mc, 1)

            # visulization other info
            start_width = int(orig_width / 20)
            start_height = int(orig_height/ 15)
            font_size = 1

            for i in range(num_class):
                point = start_width, start_height + (i * start_height)
                cv2.putText(img, actions[i] + ' : {:.2f} %'.format(actions_cnt[i] / num_frames * 100), point, cv2.FONT_HERSHEY_SIMPLEX, font_size, mc, 1)


            mesh_filename = None

                
            if save_obj:
                mesh_folder = os.path.join(output_path, 'meshes', f'{person_id:04d}')
                os.makedirs(mesh_folder, exist_ok=True)
                mesh_filename = os.path.join(mesh_folder, f'{frame_idx:06d}.obj')
                

            img = renderer.render(
                img,
                frame_verts,
                cam=frame_cam,
                color=mc,
                mesh_filename=mesh_filename,
            )

            if sideview:
                side_img = renderer.render(
                    side_img,
                    frame_verts,
                    cam=frame_cam,
                    color=mc,
                    angle=270,
                    axis=[0,1,0],
                )

        if sideview:
            img = np.concatenate([img, side_img], axis=1)

        cv2.imwrite(os.path.join(output_img_folder, f'{frame_idx:06d}.png'), img)


        if display:
            cv2.imshow('Video', img)
            if cv2.waitKey(1) & 0xFF == ord('q'):
                break

    if display:
        cv2.destroyAllWindows()

    # ========= Save rendered video ========= #
    vid_name = os.path.basename(VIDEO_FILE)
    save_name = f'{vid_name.replace(".mp4", "")}_vibe_result.mp4'
    save_name = os.path.join(output_path, save_name)
    print(f'Saving result video to {save_name}')
    images_to_video(img_folder=output_img_folder, output_vid_file=save_name)
    shutil.rmtree(output_img_folder)

shutil.rmtree(image_folder)
print('================= END =================')


  0%|          | 0/561 [00:00<?, ?it/s]

Rendering output video, writing frames to /tmp/sample_mp4_output


100%|██████████| 561/561 [01:02<00:00,  8.27it/s]


Saving result video to ./output/sample/sample_vibe_result.mp4
Running "ffmpeg -y -threads 16 -i /tmp/sample_mp4_output/%06d.png -profile:v baseline -level 3.0 -c:v libx264 -pix_fmt yuv420p -an -v error ./output/sample/sample_vibe_result.mp4"
================= END =================


In [ ]:
# Play the generated video
from IPython.display import HTML
from base64 import b64encode

def video(path):
  mp4 = open(path,'rb').read()
  data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
  return HTML('<video width=500 controls loop> <source src="%s" type="video/mp4"></video>' % data_url)

video('output/sample/sample_vibe_result.mp4')

# Get Fatness

In [ ]:
fat_scale = np.mean(pred_betas[:,1])

print(fat_scale)

fatness = None
# 0 : 심한 저체중
# 1 : 저체중
# 2 : 정상
# 3 : 과체중
# 4 : 심한 과체중

# 심한 저체중 : 4 이상 / 저체중 : 2 이상 4 미만 / 정상 : 1 이상 2 미만 / 과체중 : 0.5 이상 1 미만 / 심한 과체중 : 0.5 미만

if fat_scale >= 4:
  fatness = 0
elif fat_scale >= 2 and fat_scale < 4:
  fatness = 1
elif fat_scale >= 1 and fat_scale < 2:
  fatness = 2
elif fat_scale >= 0.5 and fat_scale < 1:
  fatness = 3
elif fat_scale < 0.5:
  fatness = 4

print(fatness)
# 0 : 심한 저체중
# 1 : 저체중
# 2 : 정상
# 3 : 과체중
# 4 : 심한 과체중

0.998605
3


# Get Consumed Kcal

In [ ]:
def get_consumed_kcal(action_cnt, FPS, fatness, real_fatness):
    run_time = action_cnt[0] / FPS
    punch_time = action_cnt[1] / FPS
    squat_time = action_cnt[2] / FPS

    run_kcal = run_time * 0.15
    punch_kcal = punch_time * 0.20
    squat_kcal = squat_time * 0.3
    
    total_kcal = run_kcal + punch_kcal + squat_kcal

    # 실제 비만도와, 예측 비만도의 평균을 이용해 비만도 결정.
    if real_fatness != -1:
        fatness = int((fatness + real_fatness) / 2)

    if fatness == 4:
        total_kcal *= 1.2
    elif fatness == 3:
        total_kcal *= 1.1
    elif fatness == 2:
        total_kcal *= 1
    elif fatness == 1:
        total_kcal *= 0.9
    elif fatness == 0:
        total_kcal *= 0.8

    return total_kcal
total_kcal = get_consumed_kcal(actions_cnt, fps, fatness, real_fatness)
print("total consumed kcal : {:.2f}".format(total_kcal))

total consumed kcal : 1.50
